In [1]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt

import os

import preprocess, fit_nn, evaluate

VA_type = "GMWB"
lapse_type = "nolapse"

cwd = f"../sim_VA/result/{VA_type}/{lapse_type}/"
save_path = f"./trainedModels/{VA_type}_PY/{lapse_type}/"

if not os.path.exists(save_path):
    os.makedirs(save_path)

price = np.load(cwd + f"outerScenarios_{VA_type}_RS_{lapse_type}.npy")
rtn = (price[:, 1:] - price[:, :-1]) / price[:, :-1]

substring_SNS = f"hedgingLoss_{VA_type}_RS_1000_{lapse_type}"

substring_lowNoise = f"hedgingLoss_{VA_type}_RS_100_{lapse_type}"
substring_mediumNoise = f"hedgingLoss_{VA_type}_RS_10_{lapse_type}"
substring_highNoise = f"hedgingLoss_{VA_type}_RS_1_{lapse_type}"

lossFiles_lowNoise = [file for file in os.listdir(cwd) if substring_lowNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_mediumNoise = [file for file in os.listdir(cwd) if substring_mediumNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_highNoise = [file for file in os.listdir(cwd) if substring_highNoise in file and os.path.isfile(os.path.join(cwd, file))]

# LoCap LSTM, LowNoise GMWB Datasets

model_name = "LSTM"
recurrent_layer_size = [32, 4]
dense_layer_size = 32
activation_function = "tanh"
lr = 0.001
dropout = 0.1
decay_rate = 0.9
patience = 100

test_size = 3000
seed = 22

n_epochs = 1000
batch_size = 4096

n_rep = 50

In [ ]:
save_name = "LSTM_LoCap_LowNoise"

for rep in range(n_rep):
    loss_file = lossFiles_lowNoise[rep]
    X_train, y_train, X_test, y_test, y_mean, y_std = preprocess.transform_data(rtn, np.load(cwd + loss_file), True, test_size, seed)

    # Build and train model
    model = fit_nn.build_model(X_train, 
                               model_name, recurrent_layer_size, dense_layer_size, 
                               activation_function, lr, dropout, decay_rate)

    path = save_path + f"{save_name}_{rep}/"
    model_trained, running_time = fit_nn.train_model(X_train, y_train, model, n_epochs, batch_size, patience, save_path)

    # Save model
    model_trained.save(path + f"trained_model")

In [2]:
# HiCap LSTM, LowNoise GMWB Datasets
model_name = "LSTM"
recurrent_layer_size = [128, 16]
dense_layer_size = 64

save_name = "LSTM_HiCap_LowNoise"

for rep in range(12, n_rep):
    loss_file = lossFiles_lowNoise[rep]
    X_train, y_train, X_test, y_test, y_mean, y_std = preprocess.transform_data(rtn, np.load(cwd + loss_file), True, test_size, seed)

    # Build and train model
    model = fit_nn.build_model(X_train, 
                               model_name, recurrent_layer_size, dense_layer_size, 
                               activation_function, lr, dropout, decay_rate)

    path = save_path + f"{save_name}_{rep}/"
    model_trained, running_time = fit_nn.train_model(X_train, y_train, model, n_epochs, batch_size, patience, save_path)

    # Save model
    model_trained.save(path + f"trained_model")

Data is split, training and test data has shape:
(47000, 240, 1) (47000,) (3000, 240, 1) (3000,)
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm (LSTM)                 (None, 240, 128)          66560     
                                                                 
 lstm_1 (LSTM)               (None, 240, 16)           9280      
                                                                 
 flatten (Flatten)           (None, 3840)              0         
                                                                 
 dense (Dense)               (None, 64)                245824    
                                                                 
 dropout (Dropout)           (None, 64)                0         
                                                                 
 dense_1 (Dense)             (None, 1)                 65        
                         

Epoch 43/1000
11/11 [==============================] - 2s 182ms/step - loss: 0.2209 - mean_squared_error: 0.2209 - val_loss: 0.2135 - val_mean_squared_error: 0.2135
Epoch 44/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.2216 - mean_squared_error: 0.2216 - val_loss: 0.2130 - val_mean_squared_error: 0.2130
Epoch 45/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.2157 - mean_squared_error: 0.2157 - val_loss: 0.2564 - val_mean_squared_error: 0.2564
Epoch 46/1000
11/11 [==============================] - 2s 182ms/step - loss: 0.2211 - mean_squared_error: 0.2211 - val_loss: 0.2124 - val_mean_squared_error: 0.2124
Epoch 47/1000
11/11 [==============================] - 2s 182ms/step - loss: 0.2216 - mean_squared_error: 0.2216 - val_loss: 0.2048 - val_mean_squared_error: 0.2048
Epoch 48/1000
11/11 [==============================] - 2s 181ms/step - loss: 0.2111 - mean_squared_error: 0.2111 - val_loss: 0.2075 - val_mean_squared_error: 0.2075
Epoch 49/1

Epoch 93/1000
11/11 [==============================] - 2s 182ms/step - loss: 0.1477 - mean_squared_error: 0.1477 - val_loss: 0.1430 - val_mean_squared_error: 0.1430
Epoch 94/1000
11/11 [==============================] - 2s 182ms/step - loss: 0.1460 - mean_squared_error: 0.1460 - val_loss: 0.1431 - val_mean_squared_error: 0.1431
Epoch 95/1000
11/11 [==============================] - 2s 187ms/step - loss: 0.1432 - mean_squared_error: 0.1432 - val_loss: 0.1434 - val_mean_squared_error: 0.1434
Epoch 96/1000
11/11 [==============================] - 2s 185ms/step - loss: 0.1513 - mean_squared_error: 0.1513 - val_loss: 0.1523 - val_mean_squared_error: 0.1523
Epoch 97/1000
11/11 [==============================] - 2s 186ms/step - loss: 0.1519 - mean_squared_error: 0.1519 - val_loss: 0.1412 - val_mean_squared_error: 0.1412
Epoch 98/1000
11/11 [==============================] - 2s 185ms/step - loss: 0.1460 - mean_squared_error: 0.1460 - val_loss: 0.1494 - val_mean_squared_error: 0.1494
Epoch 99/1

11/11 [==============================] - 2s 182ms/step - loss: 0.1000 - mean_squared_error: 0.1000 - val_loss: 0.1065 - val_mean_squared_error: 0.1065
Epoch 192/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.0998 - mean_squared_error: 0.0998 - val_loss: 0.1024 - val_mean_squared_error: 0.1024
Epoch 193/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.0971 - mean_squared_error: 0.0971 - val_loss: 0.1014 - val_mean_squared_error: 0.1014
Epoch 194/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0954 - mean_squared_error: 0.0954 - val_loss: 0.1039 - val_mean_squared_error: 0.1039
Epoch 195/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0971 - mean_squared_error: 0.0971 - val_loss: 0.1133 - val_mean_squared_error: 0.1133
Epoch 196/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.1033 - mean_squared_error: 0.1033 - val_loss: 0.1033 - val_mean_squared_error: 0.1033
Epoch 197/1000
11/1

11/11 [==============================] - 2s 181ms/step - loss: 0.0771 - mean_squared_error: 0.0771 - val_loss: 0.0885 - val_mean_squared_error: 0.0885
Epoch 290/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.0805 - mean_squared_error: 0.0805 - val_loss: 0.0921 - val_mean_squared_error: 0.0921
Epoch 291/1000
11/11 [==============================] - 2s 181ms/step - loss: 0.0828 - mean_squared_error: 0.0828 - val_loss: 0.0912 - val_mean_squared_error: 0.0912
Epoch 292/1000
11/11 [==============================] - 2s 182ms/step - loss: 0.0782 - mean_squared_error: 0.0782 - val_loss: 0.0892 - val_mean_squared_error: 0.0892
Epoch 293/1000
11/11 [==============================] - 2s 179ms/step - loss: 0.0786 - mean_squared_error: 0.0786 - val_loss: 0.0862 - val_mean_squared_error: 0.0862
Epoch 294/1000
11/11 [==============================] - 2s 181ms/step - loss: 0.0764 - mean_squared_error: 0.0764 - val_loss: 0.0893 - val_mean_squared_error: 0.0893
Epoch 295/1000
11/1

...

11/11 [==============================] - 2s 185ms/step - loss: 0.0827 - mean_squared_error: 0.0827 - val_loss: 0.0978 - val_mean_squared_error: 0.0978
Epoch 290/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0806 - mean_squared_error: 0.0806 - val_loss: 0.0929 - val_mean_squared_error: 0.0929
Epoch 291/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0780 - mean_squared_error: 0.0780 - val_loss: 0.0972 - val_mean_squared_error: 0.0972
Epoch 292/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0806 - mean_squared_error: 0.0806 - val_loss: 0.0952 - val_mean_squared_error: 0.0952
Epoch 293/1000
11/11 [==============================] - 2s 185ms/step - loss: 0.0811 - mean_squared_error: 0.0811 - val_loss: 0.1081 - val_mean_squared_error: 0.1081
Epoch 294/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0866 - mean_squared_error: 0.0866 - val_loss: 0.0987 - val_mean_squared_error: 0.0987
Epoch 295/1000
11/1

11/11 [==============================] - 2s 184ms/step - loss: 0.0700 - mean_squared_error: 0.0700 - val_loss: 0.0934 - val_mean_squared_error: 0.0934
Epoch 388/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.0768 - mean_squared_error: 0.0768 - val_loss: 0.0893 - val_mean_squared_error: 0.0893
Epoch 389/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.0759 - mean_squared_error: 0.0759 - val_loss: 0.0928 - val_mean_squared_error: 0.0928
Epoch 390/1000
11/11 [==============================] - 2s 182ms/step - loss: 0.0708 - mean_squared_error: 0.0708 - val_loss: 0.0978 - val_mean_squared_error: 0.0978
Epoch 391/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0704 - mean_squared_error: 0.0704 - val_loss: 0.0912 - val_mean_squared_error: 0.0912
Epoch 392/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0702 - mean_squared_error: 0.0702 - val_loss: 0.0910 - val_mean_squared_error: 0.0910
Epoch 393/1000
11/1

11/11 [==============================] - 2s 183ms/step - loss: 0.0617 - mean_squared_error: 0.0617 - val_loss: 0.0888 - val_mean_squared_error: 0.0888
Epoch 486/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.0614 - mean_squared_error: 0.0614 - val_loss: 0.0894 - val_mean_squared_error: 0.0894
Epoch 487/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0656 - mean_squared_error: 0.0656 - val_loss: 0.0991 - val_mean_squared_error: 0.0991
Epoch 488/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0646 - mean_squared_error: 0.0646 - val_loss: 0.0953 - val_mean_squared_error: 0.0953
Epoch 489/1000
11/11 [==============================] - 2s 184ms/step - loss: 0.0629 - mean_squared_error: 0.0629 - val_loss: 0.0900 - val_mean_squared_error: 0.0900
Epoch 490/1000
11/11 [==============================] - 2s 183ms/step - loss: 0.0628 - mean_squared_error: 0.0628 - val_loss: 0.0890 - val_mean_squared_error: 0.0890
Epoch 491/1000
11/1

INFO:tensorflow:Assets written to: ./trainedModels/GMWB_PY/nolapse/LSTM_HiCap_LowNoise_49/trained_model\assets


INFO:tensorflow:Assets written to: ./trainedModels/GMWB_PY/nolapse/LSTM_HiCap_LowNoise_49/trained_model\assets


In [1]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt

import os

import preprocess, fit_nn, evaluate

VA_type = "GMWB"
lapse_type = "nolapse"

cwd = f"../sim_VA/result/{VA_type}/{lapse_type}/"
save_path = f"./trainedModels/{VA_type}_PY/{lapse_type}/"

if not os.path.exists(save_path):
    os.makedirs(save_path)

price = np.load(cwd + f"outerScenarios_{VA_type}_RS_{lapse_type}.npy")
rtn = (price[:, 1:] - price[:, :-1]) / price[:, :-1]

substring_SNS = f"hedgingLoss_{VA_type}_RS_1000_{lapse_type}"

substring_lowNoise = f"hedgingLoss_{VA_type}_RS_100_{lapse_type}"
substring_mediumNoise = f"hedgingLoss_{VA_type}_RS_10_{lapse_type}"
substring_highNoise = f"hedgingLoss_{VA_type}_RS_1_{lapse_type}"

lossFiles_lowNoise = [file for file in os.listdir(cwd) if substring_lowNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_mediumNoise = [file for file in os.listdir(cwd) if substring_mediumNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_highNoise = [file for file in os.listdir(cwd) if substring_highNoise in file and os.path.isfile(os.path.join(cwd, file))]

# LoCap LSTM, LowNoise GMWB Datasets

model_name = "RNN"
recurrent_layer_size = [32, 4]
dense_layer_size = 32
activation_function = "tanh"
lr = 0.001
dropout = 0.1
decay_rate = 0.9
patience = 100

test_size = 3000
seed = 22

n_epochs = 1000
batch_size = 16384

n_rep = 50

save_name = "RNN_LoCap_LowNoise"

for rep in range(35, n_rep):
    loss_file = lossFiles_lowNoise[rep]
    X_train, y_train, X_test, y_test, y_mean, y_std = preprocess.transform_data(rtn, np.load(cwd + loss_file), True, test_size, seed)

    # Build and train model
    model = fit_nn.build_model(X_train, 
                               model_name, recurrent_layer_size, dense_layer_size, 
                               activation_function, lr, dropout, decay_rate)

    path = save_path + f"{save_name}_{rep}/"
    model_trained, running_time = fit_nn.train_model(X_train, y_train, model, n_epochs, batch_size, patience, save_path)

    # Save model
    model_trained.save(path + f"trained_model")
    



Data is split, training and test data has shape:
(47000, 240, 1) (47000,) (3000, 240, 1) (3000,)
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 simple_rnn (SimpleRNN)      (None, 240, 32)           1088      
                                                                 
 simple_rnn_1 (SimpleRNN)    (None, 240, 4)            148       
                                                                 
 flatten (Flatten)           (None, 960)               0         
                                                                 
 dense (Dense)               (None, 32)                30752     
                                                                 
 dropout (Dropout)           (None, 32)                0         
                                                                 
 dense_1 (Dense)             (None, 1)                 33        
                         

Epoch 44/1000
3/3 [==============================] - 3s 2s/step - loss: 0.4072 - mean_squared_error: 0.4072 - val_loss: 0.3655 - val_mean_squared_error: 0.3655
Epoch 45/1000
3/3 [==============================] - 3s 2s/step - loss: 0.3900 - mean_squared_error: 0.3900 - val_loss: 0.3751 - val_mean_squared_error: 0.3751
Epoch 46/1000
3/3 [==============================] - 4s 2s/step - loss: 0.3729 - mean_squared_error: 0.3729 - val_loss: 0.3484 - val_mean_squared_error: 0.3484
Epoch 47/1000
3/3 [==============================] - 3s 2s/step - loss: 0.3619 - mean_squared_error: 0.3619 - val_loss: 0.4066 - val_mean_squared_error: 0.4066
Epoch 48/1000
3/3 [==============================] - 3s 2s/step - loss: 0.3880 - mean_squared_error: 0.3880 - val_loss: 0.3713 - val_mean_squared_error: 0.3713
Epoch 49/1000
3/3 [==============================] - 4s 2s/step - loss: 0.3705 - mean_squared_error: 0.3705 - val_loss: 0.3877 - val_mean_squared_error: 0.3877
Epoch 50/1000
3/3 [=====================

Epoch 95/1000
3/3 [==============================] - 3s 372ms/step - loss: 0.2903 - mean_squared_error: 0.2903 - val_loss: 0.2867 - val_mean_squared_error: 0.2867
Epoch 96/1000
3/3 [==============================] - 6s 2s/step - loss: 0.2907 - mean_squared_error: 0.2907 - val_loss: 0.2841 - val_mean_squared_error: 0.2841
Epoch 97/1000
3/3 [==============================] - 4s 2s/step - loss: 0.2885 - mean_squared_error: 0.2885 - val_loss: 0.2825 - val_mean_squared_error: 0.2825
Epoch 98/1000
3/3 [==============================] - 3s 2s/step - loss: 0.2851 - mean_squared_error: 0.2851 - val_loss: 0.3012 - val_mean_squared_error: 0.3012
Epoch 99/1000
3/3 [==============================] - 4s 2s/step - loss: 0.3066 - mean_squared_error: 0.3066 - val_loss: 0.3286 - val_mean_squared_error: 0.3286
Epoch 100/1000
3/3 [==============================] - 3s 359ms/step - loss: 0.3152 - mean_squared_error: 0.3152 - val_loss: 0.3005 - val_mean_squared_error: 0.3005
Epoch 101/1000
3/3 [=============

Epoch 146/1000
3/3 [==============================] - 3s 362ms/step - loss: 0.2745 - mean_squared_error: 0.2745 - val_loss: 0.2746 - val_mean_squared_error: 0.2746
Epoch 147/1000
3/3 [==============================] - 4s 408ms/step - loss: 0.2715 - mean_squared_error: 0.2715 - val_loss: 0.2758 - val_mean_squared_error: 0.2758
Epoch 148/1000
3/3 [==============================] - 3s 350ms/step - loss: 0.2766 - mean_squared_error: 0.2766 - val_loss: 0.2742 - val_mean_squared_error: 0.2742
Epoch 149/1000
3/3 [==============================] - 6s 2s/step - loss: 0.2727 - mean_squared_error: 0.2727 - val_loss: 0.2740 - val_mean_squared_error: 0.2740
Epoch 150/1000
3/3 [==============================] - 4s 2s/step - loss: 0.2704 - mean_squared_error: 0.2704 - val_loss: 0.2827 - val_mean_squared_error: 0.2827
Epoch 151/1000
3/3 [==============================] - 4s 2s/step - loss: 0.2902 - mean_squared_error: 0.2902 - val_loss: 0.2867 - val_mean_squared_error: 0.2867
Epoch 152/1000
3/3 [=====

Epoch 247/1000
3/3 [==============================] - 3s 2s/step - loss: 0.3059 - mean_squared_error: 0.3059 - val_loss: 0.3044 - val_mean_squared_error: 0.3044
Epoch 248/1000
3/3 [==============================] - 4s 2s/step - loss: 0.2929 - mean_squared_error: 0.2929 - val_loss: 0.3267 - val_mean_squared_error: 0.3267
Epoch 249/1000
3/3 [==============================] - 3s 2s/step - loss: 0.3062 - mean_squared_error: 0.3062 - val_loss: 0.2840 - val_mean_squared_error: 0.2840
Epoch 250/1000
3/3 [==============================] - 4s 360ms/step - loss: 0.2860 - mean_squared_error: 0.2860 - val_loss: 0.2714 - val_mean_squared_error: 0.2714
Epoch 251/1000
3/3 [==============================] - 4s 400ms/step - loss: 0.2805 - mean_squared_error: 0.2805 - val_loss: 0.2995 - val_mean_squared_error: 0.2995
Epoch 252/1000
3/3 [==============================] - 6s 2s/step - loss: 0.2764 - mean_squared_error: 0.2764 - val_loss: 0.2626 - val_mean_squared_error: 0.2626
Epoch 253/1000
3/3 [========

...

3/3 [==============================] - 1s 346ms/step - loss: 0.2419 - mean_squared_error: 0.2419 - val_loss: 0.2421 - val_mean_squared_error: 0.2421
Epoch 758/1000
3/3 [==============================] - 1s 369ms/step - loss: 0.2302 - mean_squared_error: 0.2302 - val_loss: 0.2348 - val_mean_squared_error: 0.2348
Epoch 759/1000
3/3 [==============================] - 1s 358ms/step - loss: 0.2374 - mean_squared_error: 0.2374 - val_loss: 0.2409 - val_mean_squared_error: 0.2409
Epoch 760/1000
3/3 [==============================] - 1s 376ms/step - loss: 0.2450 - mean_squared_error: 0.2450 - val_loss: 0.2442 - val_mean_squared_error: 0.2442
Epoch 761/1000
3/3 [==============================] - 1s 369ms/step - loss: 0.2371 - mean_squared_error: 0.2371 - val_loss: 0.2435 - val_mean_squared_error: 0.2435
Epoch 762/1000
3/3 [==============================] - 1s 368ms/step - loss: 0.2289 - mean_squared_error: 0.2289 - val_loss: 0.2222 - val_mean_squared_error: 0.2222
Epoch 763/1000
3/3 [===========

3/3 [==============================] - 1s 369ms/step - loss: 0.2042 - mean_squared_error: 0.2042 - val_loss: 0.2090 - val_mean_squared_error: 0.2090
Epoch 808/1000
3/3 [==============================] - 1s 335ms/step - loss: 0.2068 - mean_squared_error: 0.2068 - val_loss: 0.2074 - val_mean_squared_error: 0.2074
Epoch 809/1000
3/3 [==============================] - 1s 345ms/step - loss: 0.2065 - mean_squared_error: 0.2065 - val_loss: 0.2058 - val_mean_squared_error: 0.2058
Epoch 810/1000
3/3 [==============================] - 1s 354ms/step - loss: 0.2080 - mean_squared_error: 0.2080 - val_loss: 0.2062 - val_mean_squared_error: 0.2062
Epoch 811/1000
3/3 [==============================] - 1s 364ms/step - loss: 0.2034 - mean_squared_error: 0.2034 - val_loss: 0.2052 - val_mean_squared_error: 0.2052
Epoch 812/1000
3/3 [==============================] - 1s 371ms/step - loss: 0.2036 - mean_squared_error: 0.2036 - val_loss: 0.2085 - val_mean_squared_error: 0.2085
Epoch 813/1000
3/3 [===========

3/3 [==============================] - 1s 357ms/step - loss: 0.2022 - mean_squared_error: 0.2022 - val_loss: 0.2113 - val_mean_squared_error: 0.2113
Epoch 858/1000
3/3 [==============================] - 1s 357ms/step - loss: 0.2029 - mean_squared_error: 0.2029 - val_loss: 0.2048 - val_mean_squared_error: 0.2048
Epoch 859/1000
3/3 [==============================] - 1s 354ms/step - loss: 0.2004 - mean_squared_error: 0.2004 - val_loss: 0.2013 - val_mean_squared_error: 0.2013
Epoch 860/1000
3/3 [==============================] - 1s 351ms/step - loss: 0.1995 - mean_squared_error: 0.1995 - val_loss: 0.2008 - val_mean_squared_error: 0.2008
Epoch 861/1000
3/3 [==============================] - 1s 353ms/step - loss: 0.2016 - mean_squared_error: 0.2016 - val_loss: 0.2131 - val_mean_squared_error: 0.2131
Epoch 862/1000
3/3 [==============================] - 1s 359ms/step - loss: 0.2035 - mean_squared_error: 0.2035 - val_loss: 0.2061 - val_mean_squared_error: 0.2061
Epoch 863/1000
3/3 [===========

3/3 [==============================] - 1s 358ms/step - loss: 0.2010 - mean_squared_error: 0.2010 - val_loss: 0.2040 - val_mean_squared_error: 0.2040
Epoch 908/1000
3/3 [==============================] - 1s 356ms/step - loss: 0.2002 - mean_squared_error: 0.2002 - val_loss: 0.2037 - val_mean_squared_error: 0.2037
Epoch 909/1000
3/3 [==============================] - 1s 361ms/step - loss: 0.2059 - mean_squared_error: 0.2059 - val_loss: 0.2018 - val_mean_squared_error: 0.2018
Epoch 910/1000
3/3 [==============================] - 1s 359ms/step - loss: 0.2263 - mean_squared_error: 0.2263 - val_loss: 0.2276 - val_mean_squared_error: 0.2276
Epoch 911/1000
3/3 [==============================] - 1s 363ms/step - loss: 0.2512 - mean_squared_error: 0.2512 - val_loss: 0.2691 - val_mean_squared_error: 0.2691
Epoch 912/1000
3/3 [==============================] - 1s 359ms/step - loss: 0.2518 - mean_squared_error: 0.2518 - val_loss: 0.2341 - val_mean_squared_error: 0.2341
Epoch 913/1000
3/3 [===========

3/3 [==============================] - 1s 375ms/step - loss: 0.1956 - mean_squared_error: 0.1956 - val_loss: 0.2026 - val_mean_squared_error: 0.2026
Epoch 958/1000
3/3 [==============================] - 1s 372ms/step - loss: 0.1981 - mean_squared_error: 0.1981 - val_loss: 0.2036 - val_mean_squared_error: 0.2036
Epoch 959/1000
3/3 [==============================] - 1s 380ms/step - loss: 0.1955 - mean_squared_error: 0.1955 - val_loss: 0.2057 - val_mean_squared_error: 0.2057
Epoch 960/1000
3/3 [==============================] - 1s 358ms/step - loss: 0.1944 - mean_squared_error: 0.1944 - val_loss: 0.2011 - val_mean_squared_error: 0.2011
INFO:tensorflow:Assets written to: ./trainedModels/GMWB_PY/nolapse/RNN_LoCap_LowNoise_49/trained_model\assets


In [3]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt

import os

import preprocess, fit_nn, evaluate

VA_type = "GMWB"
lapse_type = "nolapse"

cwd = f"../sim_VA/result/{VA_type}/{lapse_type}/"
save_path = f"./trainedModels/{VA_type}_PY/{lapse_type}/"

if not os.path.exists(save_path):
    os.makedirs(save_path)

price = np.load(cwd + f"outerScenarios_{VA_type}_RS_{lapse_type}.npy")
rtn = (price[:, 1:] - price[:, :-1]) / price[:, :-1]

substring_SNS = f"hedgingLoss_{VA_type}_RS_1000_{lapse_type}"

substring_lowNoise = f"hedgingLoss_{VA_type}_RS_100_{lapse_type}"
substring_mediumNoise = f"hedgingLoss_{VA_type}_RS_10_{lapse_type}"
substring_highNoise = f"hedgingLoss_{VA_type}_RS_1_{lapse_type}"

lossFiles_lowNoise = [file for file in os.listdir(cwd) if substring_lowNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_mediumNoise = [file for file in os.listdir(cwd) if substring_mediumNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_highNoise = [file for file in os.listdir(cwd) if substring_highNoise in file and os.path.isfile(os.path.join(cwd, file))]

# LoCap LSTM, LowNoise GMWB Datasets

model_name = "FFN"
recurrent_layer_size = [128, 16]
dense_layer_size = 32
activation_function = "ReLU"
lr = 0.001
dropout = 0.1
decay_rate = 0.9
patience = 10

test_size = 3000
seed = 22

n_epochs = 1000
batch_size = 4096

n_rep = 50

save_name = "FNN_LoCap_LowNoise"

for rep in range(n_rep):
    loss_file = lossFiles_lowNoise[rep]
    X_train, y_train, X_test, y_test, y_mean, y_std = preprocess.transform_data(rtn, np.load(cwd + loss_file), True, test_size, seed, model="FNN")

    # Build and train model
    model = fit_nn.build_model(X_train, 
                               model_name, recurrent_layer_size, dense_layer_size, 
                               activation_function, lr, dropout, decay_rate)

    path = save_path + f"{save_name}_{rep}/"
    model_trained, running_time = fit_nn.train_model(X_train, y_train, model, n_epochs, batch_size, patience, save_path)

    # Save model
    model_trained.save(path + f"trained_model")
    



Data is split, training and test data has shape:
(47000, 240) (47000,) (3000, 240) (3000,)
Model: "sequential_150"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_300 (Dense)           (None, 128)               30848     
                                                                 
 dropout_150 (Dropout)       (None, 128)               0         
                                                                 
 dense_301 (Dense)           (None, 16)                2064      
                                                                 
 dropout_151 (Dropout)       (None, 16)                0         
                                                                 
 dense_302 (Dense)           (None, 1)                 17        
                                                                 
Total params: 32,929
Trainable params: 32,929
Non-trainable params: 0
_______________________

11/11 [==============================] - 0s 7ms/step - loss: 0.2477 - mean_squared_error: 0.2477 - val_loss: 0.3379 - val_mean_squared_error: 0.3379
Epoch 45/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2470 - mean_squared_error: 0.2470 - val_loss: 0.3358 - val_mean_squared_error: 0.3358
Epoch 46/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2440 - mean_squared_error: 0.2440 - val_loss: 0.3337 - val_mean_squared_error: 0.3337
Epoch 47/1000
11/11 [==============================] - 0s 8ms/step - loss: 0.2395 - mean_squared_error: 0.2395 - val_loss: 0.3322 - val_mean_squared_error: 0.3322
Epoch 48/1000
11/11 [==============================] - 0s 9ms/step - loss: 0.2390 - mean_squared_error: 0.2390 - val_loss: 0.3312 - val_mean_squared_error: 0.3312
Epoch 49/1000
11/11 [==============================] - 0s 11ms/step - loss: 0.2327 - mean_squared_error: 0.2327 - val_loss: 0.3294 - val_mean_squared_error: 0.3294
Epoch 50/1000
11/11 [==============

INFO:tensorflow:Assets written to: ./trainedModels/GMWB_PY/nolapse/FNN_LoCap_LowNoise_0/trained_model\assets


Data is split, training and test data has shape:
(47000, 240) (47000,) (3000, 240) (3000,)
Model: "sequential_151"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_303 (Dense)           (None, 128)               30848     
                                                                 
 dropout_152 (Dropout)       (None, 128)               0         
                                                                 
 dense_304 (Dense)           (None, 16)                2064      
                                                                 
 dropout_153 (Dropout)       (None, 16)                0         
                                                                 
 dense_305 (Dense)           (None, 1)                 17        
                                                                 
Total params: 32,929
Trainable params: 32,929
Non-trainable params: 0
_______________________

11/11 [==============================] - 0s 7ms/step - loss: 0.2622 - mean_squared_error: 0.2622 - val_loss: 0.3485 - val_mean_squared_error: 0.3485
Epoch 45/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2567 - mean_squared_error: 0.2567 - val_loss: 0.3468 - val_mean_squared_error: 0.3468
Epoch 46/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2565 - mean_squared_error: 0.2565 - val_loss: 0.3464 - val_mean_squared_error: 0.3464
Epoch 47/1000
11/11 [==============================] - 0s 8ms/step - loss: 0.2541 - mean_squared_error: 0.2541 - val_loss: 0.3453 - val_mean_squared_error: 0.3453
Epoch 48/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2500 - mean_squared_error: 0.2500 - val_loss: 0.3437 - val_mean_squared_error: 0.3437
Epoch 49/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2476 - mean_squared_error: 0.2476 - val_loss: 0.3437 - val_mean_squared_error: 0.3437
Epoch 50/1000
11/11 [===============

...

11/11 [==============================] - 0s 7ms/step - loss: 0.2438 - mean_squared_error: 0.2438 - val_loss: 0.3358 - val_mean_squared_error: 0.3358
Epoch 45/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2431 - mean_squared_error: 0.2431 - val_loss: 0.3350 - val_mean_squared_error: 0.3350
Epoch 46/1000
11/11 [==============================] - 0s 8ms/step - loss: 0.2406 - mean_squared_error: 0.2406 - val_loss: 0.3357 - val_mean_squared_error: 0.3357
Epoch 47/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2365 - mean_squared_error: 0.2365 - val_loss: 0.3334 - val_mean_squared_error: 0.3334
Epoch 48/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2322 - mean_squared_error: 0.2322 - val_loss: 0.3329 - val_mean_squared_error: 0.3329
Epoch 49/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2322 - mean_squared_error: 0.2322 - val_loss: 0.3294 - val_mean_squared_error: 0.3294
Epoch 50/1000
11/11 [===============

INFO:tensorflow:Assets written to: ./trainedModels/GMWB_PY/nolapse/FNN_LoCap_LowNoise_48/trained_model\assets


Data is split, training and test data has shape:
(47000, 240) (47000,) (3000, 240) (3000,)
Model: "sequential_199"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_447 (Dense)           (None, 128)               30848     
                                                                 
 dropout_248 (Dropout)       (None, 128)               0         
                                                                 
 dense_448 (Dense)           (None, 16)                2064      
                                                                 
 dropout_249 (Dropout)       (None, 16)                0         
                                                                 
 dense_449 (Dense)           (None, 1)                 17        
                                                                 
Total params: 32,929
Trainable params: 32,929
Non-trainable params: 0
_______________________

Epoch 44/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2469 - mean_squared_error: 0.2469 - val_loss: 0.3429 - val_mean_squared_error: 0.3429
Epoch 45/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2432 - mean_squared_error: 0.2432 - val_loss: 0.3420 - val_mean_squared_error: 0.3420
Epoch 46/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2398 - mean_squared_error: 0.2398 - val_loss: 0.3411 - val_mean_squared_error: 0.3411
Epoch 47/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2354 - mean_squared_error: 0.2354 - val_loss: 0.3380 - val_mean_squared_error: 0.3380
Epoch 48/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2342 - mean_squared_error: 0.2342 - val_loss: 0.3384 - val_mean_squared_error: 0.3384
Epoch 49/1000
11/11 [==============================] - 0s 7ms/step - loss: 0.2310 - mean_squared_error: 0.2310 - val_loss: 0.3348 - val_mean_squared_error: 0.3348
Epoch 50/1000
11/11 [=

INFO:tensorflow:Assets written to: ./trainedModels/GMWB_PY/nolapse/FNN_LoCap_LowNoise_49/trained_model\assets


In [ ]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt

import os

import preprocess, fit_nn, evaluate

VA_type = "GMWB"
lapse_type = "nolapse"

cwd = f"../sim_VA/result/{VA_type}/{lapse_type}/"
save_path = f"./trainedModels/{VA_type}_PY/{lapse_type}/"

if not os.path.exists(save_path):
    os.makedirs(save_path)

price = np.load(cwd + f"outerScenarios_{VA_type}_RS_{lapse_type}.npy")
rtn = (price[:, 1:] - price[:, :-1]) / price[:, :-1]

substring_SNS = f"hedgingLoss_{VA_type}_RS_1000_{lapse_type}"

substring_lowNoise = f"hedgingLoss_{VA_type}_RS_100_{lapse_type}"
substring_mediumNoise = f"hedgingLoss_{VA_type}_RS_010_{lapse_type}"
substring_highNoise = f"hedgingLoss_{VA_type}_RS_001_{lapse_type}"

lossFiles_lowNoise = [file for file in os.listdir(cwd) if substring_lowNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_mediumNoise = [file for file in os.listdir(cwd) if substring_mediumNoise in file and os.path.isfile(os.path.join(cwd, file))]
lossFiles_highNoise = [file for file in os.listdir(cwd) if substring_highNoise in file and os.path.isfile(os.path.join(cwd, file))]

# LoCap LSTM, mediumNoise GMWB Datasets

model_name = "LSTM"
recurrent_layer_size = [32, 4]
dense_layer_size = 32
activation_function = "tanh"
lr = 0.001
dropout = 0.1
decay_rate = 0.9
patience = 100

test_size = 3000
seed = 22

n_epochs = 1000
batch_size = 4096

n_rep = 50

save_name = "LSTM_LoCap_mediumNoise"

for rep in range(n_rep):
    loss_file = lossFiles_mediumNoise[rep]
    X_train, y_train, X_test, y_test, y_mean, y_std = preprocess.transform_data(rtn, np.load(cwd + loss_file), True, test_size, seed)

    # Build and train model
    model = fit_nn.build_model(X_train, 
                               model_name, recurrent_layer_size, dense_layer_size, 
                               activation_function, lr, dropout, decay_rate)

    path = save_path + f"{save_name}_{rep}/"
    model_trained, running_time = fit_nn.train_model(X_train, y_train, model, n_epochs, batch_size, patience, save_path)

    # Save model
    model_trained.save(path + f"trained_model")


# HiCap LSTM, mediumNoise GMWB Datasets
model_name = "LSTM"
recurrent_layer_size = [128, 16]
dense_layer_size = 64

save_name = "LSTM_HiCap_mediumNoise"

for rep in range(n_rep):
    loss_file = lossFiles_mediumNoise[rep]
    X_train, y_train, X_test, y_test, y_mean, y_std = preprocess.transform_data(rtn, np.load(cwd + loss_file), True, test_size, seed)

    # Build and train model
    model = fit_nn.build_model(X_train, 
                               model_name, recurrent_layer_size, dense_layer_size, 
                               activation_function, lr, dropout, decay_rate)

    path = save_path + f"{save_name}_{rep}/"
    model_trained, running_time = fit_nn.train_model(X_train, y_train, model, n_epochs, batch_size, patience, save_path)

    # Save model
    model_trained.save(path + f"trained_model")
